Ce calepin est composé de deux parties :

1. la première partie est une rapide présentation du $\lambda$-calcul illustrée par l'utilisation d'un module permettant de définir et transformer des $\lambda$-termes.
2. la deuxième partie reprend la partie « pouvoir d'expression du $\lambda$-calcul » en l'illustrant avec les lambda-expressions du langage Python.

# $\lambda$-calcul

Le [$\lambda$-calcul](https://fr.wikipedia.org/wiki/Lambda-calcul) a été introduit dans les années 1930, principalement par [Alonzo Church](https://fr.wikipedia.org/wiki/Alonzo_Church) pour des questions de fondements mathématiques, semblables à celles qui ont conduit, à la même époque, [Alan Turing](https://fr.wikipedia.org/wiki/Alan_Turing) à concevoir les [machines](https://fr.wikipedia.org/wiki/Machine_de_Turing) qui portent son nom maintenant.

Avec les machines de Turing, le $\lambda$-calcul est l'un des principaux outils permettant d'étudier l'informatique théorique. Il est en particulier le fondement de la programmation fonctionnelle, et des langages de programmation comme [Lisp](https://fr.wikipedia.org/wiki/Lisp), [Scheme](https://fr.wikipedia.org/wiki/Scheme), [ML](https://fr.wikipedia.org/wiki/ML_(langage)), [Haskell](https://fr.wikipedia.org/wiki/Haskell) lui doivent beaucoup.

## Les $\lambda$-termes

Sommaire de cette partie :

* définition des $\lambda$-termes
* variables libres, liées. Sous-termes

Le tout illustré avec une classe Python pour représenter et manipuler des $\lambda$-termes.

### Définition des $\lambda$-termes

En principe, les $\lambda$-termes sont des mots sur lesquels certaines opérations sont possibles. Ces mots ont vocation à pouvoir exprimer des fonctions, ainsi que leur application à un argument. 

Formellement, l'alphabet $\Sigma$ utilisé pour les $\lambda$-termes est constitué :

* d'un ensemble infini dénombrable de variables $V=\{x, y, z, t, ...\}$ ;
* et d'un ensemble de cinq symboles $\mathcal{S}=\{\lambda, ., (, ), ESP\}$, $ESP$ désignant l'espace.
Ainsi $\Sigma = V\cup \mathcal{S}$.

Les $\lambda$-termes sont construits inductivement à l'aide des trois règles

1. toute variable est un $\lambda$-terme ;
2. si $T$ est un $\lambda$-terme et $x$ une variable, alors $\lambda x.T$ est un $\lambda$-terme, que l'on appelle *abstraction* de $T$ par $x$ ;
3. si $T$ et $S$ sont deux $\lambda$-termes, alors $(T\ S)$ est un $\lambda$-terme, que l'on appelle *application* de $T$ à $S$.

L'ensemble $\Lambda$ des $\lambda$-termes est donc le plus petit sous-ensemble de $\Sigma^*$ contenant $V$ et stable par abstraction et application.

### Une classe pour les $\lambda$-termes

Le module `lambda_calcul` définit une classe `Lambda_terme` permettant de construire et manipuler des objets représentant des $\lambda$-termes.

**Remarque :** ce module fait appel au module`sly` qui permet de définir des analyseurs lexicaux et syntaxiques. Ce module doit donc être préalablement installé (`pip install sly`).

In [1]:
from lambda_calcul import Lambda_terme

### Construction de $\lambda$-termes

L'une des façons les plus simples de construire des $\lambda$-termes est d'invoquer le constructeur `Lambda_terme` avec une chaîne de caractères les représentant. 

In [2]:
T1 = Lambda_terme("x")
T2 = Lambda_terme("(x x)")
T3 = Lambda_terme("!x.x")
T4 = Lambda_terme('!x.(x y)')
T5 = Lambda_terme('(!x.(x y) x)')

Les objets de la classe `Lambda_terme` peuvent être convertis en chaînes de caractères et imprimés.

In [3]:
termes = (T1, T2, T3, T4, T5)
for t in termes:
    print(t)

x
(x x)
λx.x
λx.(x y)
(λx.(x y) x)


La syntaxe autorisée pour les $\lambda$-termes est

1. pour les variables : n'importe quelles chaîne de caractères ne contenant que des lettres (latins) non accentuées majuscules ou minuscules, ainsi que des chiffres. Autrement dit n'importe quelle chaîne correspondant à l'expression régulière `[A-Za-z][A-Za-z0-9]*`.
2. pour les abstractions : n'importe quelle chaîne débutant par `!` ou $\lambda$ suivie d'une variable, suivie d'un point `.` suivi d'une chaîne décrivant un $\lambda$-terme. Autrement dit n'importe quelle chaîne satisfaisant `(!|λ)VAR.LAMBDA-TERME`.
3. pour les applications : n'importe quelle chaîne débutant par une parenthèse ouvrante `(` et terminant par une parenthèse fermante `)` et comprenant entre les deux la description de deux $\lambda$-termes séparés par un ou plusieurs espaces. Autrement dit n'importe quelle chaîne satisfaisant `(LAMBDA-TERME ESPACES LAMBDA-TERME)`.

**Remarque :** le parenthésage des applications est obligatoire, contrairement à la convention d'associativité à gauche qui permet usuellement d'écrire $M\ N\ P$ au lieu de $((M\ N)\ P)$.
De même deux abstractions successives doivent être explicitement écrites : il n'est pas possible d'écrire $\lambda xy.(x\ y)$, il faut écrire $\lambda x.\lambda y.(x\ y)$.

Les passages à la ligne sont autorisés dans la chaîne transmise au constructeur.

In [4]:
print(Lambda_terme('''(james
                   bond007)'''))

(james bond007)


L'exception `LambdaSyntaxError` est déclenchée en cas de présence de caractères non autorisés ou de malformation syntaxique.

In [5]:
# Lambda_terme('bond 007')

In [6]:
# Lambda_terme('(james bond007 !)')

### Autres constructions

Deux méthodes permettent de construire de nouveaux $\lambda$-termes à partir de $\lambda$-termes existant.

La méthode `abstrait` permet de construire une abstraction.

In [7]:
print(T1.abstrait('x'))
print(T2.abstrait('y'))

λx.x
λy.(x x)


La méthode `applique` construit une application d'un terme sur un autre.

In [8]:
print(T2.applique(T3))
print(T3.applique(T2))

((x x) λx.x)
(λx.x (x x))


### Quelques prédicats

Trois prédicats `est_variable`, `est_abstraction` et `est_application` permettent de reconnaître la nature d'un $\lambda$-terme.

In [9]:
# pour rappel des termes définis
for t in termes:
    print(t)

x
(x x)
λx.x
λx.(x y)
(λx.(x y) x)


In [10]:
tuple(t.est_variable() for t in termes)

(True, False, False, False, False)

In [11]:
tuple(t.est_abstraction() for t in termes)

(False, False, True, True, False)

In [12]:
tuple(t.est_application() for t in termes)

(False, True, False, False, True)

### Variables libres, variables liées

Parmi les variables figurant dans un $\lambda$-terme, certaines sont dites *libres*, et d'autres *liées*.

Les variables libres sont celles qui ne sont pas sous la portée d'une abstraction. L'ensemble $FV(T)$ des variables libres d'un $\lambda$-terme $T$ est défini inductivement par les trois règles :

1. $FV(x) = \{x\}$.
2. $FV(\lambda x.T) = FV(T)\setminus\{x\}$.
3. $FV((T_1\ T_2)) = FV(T_1)\cup FV(T_2)$.

Les variables liées sont celles qui sont sous la portée d'une abstraction. L'ensemble $BV(T)$ des variables liées d'un  $\lambda$-terme $T$ est défini inductivement par les trois règles :

1. $BV(x) = \emptyset$.
2. $BV(\lambda x.T) = BV(T)\cup \{x\}$ si $x\in FV(T)$, sinon
   $BV(\lambda x.T) = BV(T)$.
3. $BV((T_1\ T_2)) = BV(T_1)\cup BV(T_2)$.

La méthode `variables` donne sous un couple constitué de l'ensemble des variables libres et de l'ensemble des variables liées du $\lambda$-terme.

In [13]:
tuple(t.variables() for t in termes)

(({'x'}, set()),
 ({'x'}, set()),
 (set(), {'x'}),
 ({'y'}, {'x'}),
 ({'x', 'y'}, {'x'}))

**Remarque :** Dans un $\lambda$-terme, une variable peut être à la fois libre et liée comme le montre l'exemple du terme `T5` qui contient deux occurrences de la variable $x$, la première étant liée et la seconde libre. Pour être plus précis, on devrait plutôt parler d'*occurrence libre* ou *liée* d'une variable.

Un $\lambda$-terme sans variable libre est appelé *terme clos*, ou encore *combinateur*.

### Sous-termes

Hormis les variables, les $\lambda$-termes sont construits à partir d'autres $\lambda$-termes qui eux-mêmes peuvent être construits à l'aide d'autres $\lambda$-termes encore. 

Un $\lambda$-terme contient donc des *sous-termes*.

Voici comment l'ensemble $ST$ des sous-termes d'un $\lambda$-terme est défini inductivement selon la structure de ce terme.

1. Les variables n'ont qu'un seul sous-terme : elles-mêmes. $ST(x) = \{x\}$.
2. Les sous-termes d'une abstraction sont, outre l'abstration elle-même, les sous-termes de son corps. $ST(\lambda x.T) = \{\lambda x.T\}\cup ST(T)$.
3. Les sous-termes d'une application sont, outre l'application elle-même, les sous-termes des deux termes la composant. $ST((T_1\ T_2)) = \{(T_1\ T_2)\}\cup ST(T_1)\cup ST(T_2)$.

La méthode `sous_termes` donne la liste des sous-termes d'un $\lambda$-terme. L'ordre dans lequel figurent les sous-termes dans cette liste est l'ordre d'apparition de ces sous-termes dans une lecture de gauche à droite (autrement dit, un ordre préfixe).

In [14]:
for t in T5.sous_termes():
    print(t)

(λx.(x y) x)
λx.(x y)
(x y)
x
y
x


## $\beta$-réduction ou calculer avec des $\lambda$-termes

### Substitution

Étant donnés deux $\lambda$-termes $T$ et $R$, et une variable $x$, on note $T[x:= R]$ le $\lambda$-terme obtenu en substituant le terme $R$ à toutes les occurrences libres de la variable $x$ dans le terme $T$.

1. Si $T$ est une variable, $T[x:=R] = R$ si $T=x$ et $T[x := R] = T$ si $T\neq x$.
2. Si $T=(T_1\ T_2)$ est une application, $T[x:=R] = (T_1[x:=R]\ T_2[x := R])$.
3. Si $T=\lambda y.S$ est une abstraction, alors il faut distinguer deux cas pour définir $T[x:=R]$
    
    * si $y\not\in FV(R)$, alors $T[x:=R] = \lambda y.S[x:= R]$.
    * si $y\in FV(R)$, alors $T[x:=R] = \lambda z.S[y:=z][x:=R]$, la variable $z$ étant une nouvelle variable n'apparaissant pas dans $S$ ni dans $R$. On procède à un renommage de la variable d'abstraction ($y$) pour éviter que les occurrences libres de $y$ de $R$ n'entrent sous la portée de l'abstraction.

La méthode `subs` renvoie le terme obtenu en substituant un $\lambda$-terme à  toutes les occurrences libres d'une variable.

In [15]:
# substitution dans une variable
print('T1 = {:s}'.format(str(T1)))
x = 'y'; R = Lambda_terme('(y x)')
print('T1[{:s}:={:s}] = {:s}'.format(x, str(R), str(T1.subs(x, R))))
x = 'x'
print('T1[{:s}:={:s}] = {:s}'.format(x, str(R), str(T1.subs(x, R))))

T1 = x
T1[y:=(y x)] = x
T1[x:=(y x)] = (y x)


In [16]:
# substitution dans une application
print('T2 = {:s}'.format(str(T2)))
x = 'y'; R = Lambda_terme('(y x)')
print('T2[{:s}:={:s}] = {:s}'.format(x, str(R), str(T2.subs(x, R))))
x = 'x'
print('T2[{:s}:={:s}] = {:s}'.format(x, str(R), str(T2.subs(x, R))))

T2 = (x x)
T2[y:=(y x)] = (x x)
T2[x:=(y x)] = ((y x) (y x))


In [17]:
# substitution dans une abstraction
print('T4 = {:s}'.format(str(T4)))
x = 'x'; R = Lambda_terme('(y z)')
print('T4[{:s}:={:s}] = {:s}'.format(x, str(R), str(T4.subs(x, R))))
x = 'y'; R = Lambda_terme('(y z)')
print('T4[{:s}:={:s}] = {:s}'.format(x, str(R), str(T4.subs(x, R))))
x = 'y'; R = Lambda_terme('(y x)')
print('T4[{:s}:={:s}] = {:s}'.format(x, str(R), str(T4.subs(x, R))))

T4 = λx.(x y)
T4[x:=(y z)] = λx.(x y)
T4[y:=(y z)] = λx.(x (y z))
T4[y:=(y x)] = λx0.(x0 (y x))


**Remarque :** on peut utiliser la substitution pour construire des $\lambda$-termes à partir d'autres existants. 

In [18]:
print(Lambda_terme('(!z.(T2 T3) T4)').subs('T2', T2).subs('T3', T3).subs('T4', T4))

(λz.((x x) λx.x) λx.(x y))


### Réduire un terme

L'idée principale qui motive la notion de réduction est qu'une abstraction $\lambda x.T$ représente une fonction $x \mapsto T$, et qu'une application d'une abstraction à un terme $R$, $(\lambda x.T\ R)$ représente l'application de la fonction au terme $R$.

De la même façon que l'application la fonction $x\mapsto x^2+2x -1$ à un nombre $y$ se ramène au calcul de l'expression $y^2+2y-1$ obtenue en substituant $y$ à $x$, l'application $(\lambda x.T\ R)$ doit se réduire au terme $T[x:=R]$.

Un terme de la forme $(\lambda x.T\ R)$, autrement dit une application d'une abstraction à un terme, est appelé *redex*.

La *réduction d'un redex* est une relation, notée $\rightarrow_\beta$, est définie par

$$ (\lambda x.T\ R) \rightarrow_\beta T[x:=R].$$ 

On peut étendre cette notion de réduction à tout $\lambda$-terme dont l'un au moins de ses sous-termes est un redex. Le terme réduit correspondant étant celui obtenu en remplaçant un sous-terme redex par son réduit.

Selon cette définition, seuls les $\lambda$-termes ayant au moins un redex parmi leurs sous-termes peuvent être réduits. Les $\lambda$-termes ne contenant aucun redex sont dit *irréductibles* ou encore sont des *formes normales*.

La méthode `est_redex` permet de distinguer les $\lambda$-termes qui sont des redex.

In [19]:
for t in termes:
    print(t, t.est_redex())

x False
(x x) False
λx.x False
λx.(x y) False
(λx.(x y) x) True


In [20]:
T6 = T4.applique(T5)
for t in T6.sous_termes():
    print(t, t.est_redex())

(λx.(x y) (λx.(x y) x)) True
λx.(x y) False
(x y) False
x False
y False
(λx.(x y) x) True
λx.(x y) False
(x y) False
x False
y False
x False


La méthode `reduit` réduit les redex. La valeur de l'expression `T.reduit()` est un couple (Lambda_terme, bool) dont la valeur dépend du $\lambda$-terme `T` :

* si `T` contient un redex, alors le booléen a la valeur `True` et la première composante du couple est le $\lambda$-terme obtenu en remplaçant le redex le plus à gauche dans `T` par le terme obtenu par une étape de réduction.
* si `T` ne contient aucun redex, alors le couple est `(T, False)`.

In [21]:
t, reduit = T2.reduit()
print(T2)
print(reduit)
print(t)

(x x)
False
(x x)


In [22]:
T7, reduit = T6.reduit()
print(T6)
print(reduit)
print(T7)

(λx.(x y) (λx.(x y) x))
True
((λx.(x y) x) y)


Le terme `T6` contient deux redex. Comme il a été signalé la méthode `reduit` réduit le redex le plus à gauche, et dans le cas de `T6` le redex le plus à gauche est `T6` lui-même. Et cela donne le terme `T7`.

Mais comme `T6 = (T4 T5)`, et que `T5` est un redex, considérons le terme `(T4 T5')` dans lequel `T5'` est le terme obtenu en réduisant le redex `T5`.

In [23]:
T5bis, reduit = T5.reduit()
T7bis = T4.applique(T5bis)
print(T5)
print
print(T7bis)

(λx.(x y) x)
(λx.(x y) (x y))


Nous voyons donc qu'un $\lambda$-terme peut se réduire de plusieurs façons (en fait d'autant de façon que le terme contient de sous-termes qui sont des redex).

En particulier nous avons

* `T6` $\rightarrow_\beta$ `T7` et
* `T6` $\rightarrow_\beta$ `T7bis`.

Si nous envisageons les $\beta$ reductions comme des étapes de calcul, nous avons donc deux voies distinctes pour « calculer » `T6`. 

Poursuivons le calcul pour chacun des deux termes `T7` et `T7bis` qui ne sont pas des formes normales.

In [24]:
T8, _ = T7.reduit()
T8bis, _ = T7bis.reduit()
print('{} = {} : {}'.format(str(T8), str(T8bis), T8==T8bis))

((x y) y) = ((x y) y) : True


Après une nouvelle étape de réduction nous obtenons le même terme $((x\ y)\ y)$ qui est irréductible.
On peut dire que par deux calculs différents `T6` se calcule, ou se *normalise*, en $((x\ y)\ y)$.
On écrit

$$ \mathtt{T6} \twoheadrightarrow_{\beta} ((x\ y)\ y),$$
la notation $T\twoheadrightarrow_{\beta} R$ signifiant qu'il y a un nombre quelconque (y compris nul) d'étapes de $\beta$-réduction pour arriver au terme $R$ en partant de $T$ (dit en terme plus savant, la relation $\twoheadrightarrow_\beta$ est la clôture réflexive et transitive de la relation $\rightarrow_\beta$).

### Formes normales, normalisation

On dit d'un $\lambda$-terme $T$ qu'il est *normalisable* s'il existe un $\lambda$-terme $R$ irréductible tel que

$$ T\twoheadrightarrow_{\beta} R.$$
Dans ce cas, on dit que $R$ est une *forme normale* de $T$.

Par exemple, `T6` est normalisable et admet $((x\ y)\ y)$ pour forme normale.

Deux questions se posent naturellement :

1. est-ce que tout $\lambda$-terme est normalisable ?
2. un $\lambda$-terme normalisable peut-il avoir plusieurs formes normales ?

La réponse à la première question est négative. Il suffit pour s'en convaincre de considérer le terme

$$\Omega = (\lambda x.(x\ x)\ \lambda x.(x\ x)),$$
qui est un redex et est donc réductible.

In [25]:
OMEGA = Lambda_terme('(!x.(x x) !x.(x x))')
print(OMEGA)
t, reduit = OMEGA.reduit()
print(reduit)
print('{} -> {}'.format(str(OMEGA), str(t)))
print(t==OMEGA)

(λx.(x x) λx.(x x))
True
(λx.(x x) λx.(x x)) -> (λx.(x x) λx.(x x))
True


Le terme $\Omega$ n'a qu'un seul redex. Il n'y a donc qu'une seule façon de le réduire et cette réduction donne le terme $\Omega$ lui-même. Quelque soit le nombre d'étapes de réduction qu'on effectue on garde toujours le même terme : $\Omega$ n'est donc pas normalisable. 

Il existe donc des termes non normalisables, et $\Omega$ en est un exemple les plus simples.

Venons-en maintenant à la deuxième question : un terme normalisable peut-il avoir plusieurs formes normales ?

Cette question est naturelle puisque lorsqu'un $\lambda$-terme possède plusieurs redex, il y a plusieurs façons de le réduire, et il se pourrait bien que ces voies différentes mènent à des formes normales différentes.

Cela n'a pas été le cas pour le terme `T6`. Et il se trouve que cet exemple particulier reflète la situation générale, car la relation de $\beta$-réduction satisfait une propriété qu'on appelle propriété du diamant.

**Propriété du diamant** Soit $T$ un $\lambda$-terme qui peut se réduire en un nombre fini d'étapes en deux termes différents $R_1$ et $R_2$. Alors il existe un terme $R$ en lequel chacun des deux termes $R_1$ et $R_2$ se réduit en un nombre quelconque (y compris nul) d'étapes.

Cette propriété doit son nom à la figure qui l'illustre. Cette propriété est aussi connue sous le nom de *confluence* de la $\beta$-réduction.

![illustration de la propriété du diamant](tikz_diamant.png)

**Conséquence de la propriété du diamant :** Un $\lambda$-terme normalisable ne peut avoir qu'une seule forme normale.

Maintenant que nous avons répondu aux deux questions que nous nous sommes posées, il en vient une troisième.

Étant donné que certains $\lambda$-termes sont normalisables et d'autres non, y a-t-il un moyen de les reconnaître ?

Si par *moyen* nous entendons un algorithme général prenant un $\lambda$-terme en entrée, et répondant OUI si ce terme est normalisable et NON dans le cas contraire, alors la réponse est non. Aucun algorithme ne permet de distinguer les termes normalisables de ceux qui ne le sont pas. Le problème de la reconnaissance des termes normalisables est *indécidable*.

Dit en d'autres termes, l'ensemble des termes normalisables n'est pas récursif. En revanche il est récursivement énumérable. En effet, si un terme est normalisable, pour s'en rendre compte il suffit de suivre tous les chemins de réduction. L'un d'eux mène à un terme irréductible et on le trouvera en un nombre fini d'étapes.

La méthode `forme_normale` calcule la forme normale d'un terme normalisable si ce terme l'est, et ne renvoie rien dans le cas contraire. 

In [26]:
print(T6.forme_normale())

((x y) y)


In [27]:
print(OMEGA.forme_normale())

None


Hmmmm ... Comment est-ce possible puisque nous venons de voir qu'aucun algorithme ne permet de décider si un terme est normalisable ?

En fait le nombre d'étapes de réduction dans le calcul d'une forme normale est limité (par défaut à 100 étapes maximum). On peut visualiser chaque étape de calcul avec le paramètre optionnel `verbose` auquel il faut attribuer la valeur `True`.

In [28]:
T6.forme_normale(verbose=True)

(λx.(x y) (λx.(x y) x))
  1: ---> (λx.(x y) (λx.(x y) x))
  2: ---> ((λx.(x y) x) y)
  3: ---> ((x y) y)
Forme normale calculée : ((x y) y)


On voit que la forme normale du terme `T6` est calculé en trois étapes.

Pour un terme non normalisable les calculs peuvent (en principe) être infinis. Voici la tentative de détermination d'une forme normale pour le terme $\Omega$ limité à dix étapes à l'aide du paramètre optionnel `nb_etapes_max`. 

In [29]:
OMEGA.forme_normale(verbose=True, nb_etapes_max=10)

(λx.(x x) λx.(x x))
  1: ---> (λx.(x x) λx.(x x))
  2: ---> (λx.(x x) λx.(x x))
  3: ---> (λx.(x x) λx.(x x))
  4: ---> (λx.(x x) λx.(x x))
  5: ---> (λx.(x x) λx.(x x))
  6: ---> (λx.(x x) λx.(x x))
  7: ---> (λx.(x x) λx.(x x))
  8: ---> (λx.(x x) λx.(x x))
  9: ---> (λx.(x x) λx.(x x))
 10: ---> (λx.(x x) λx.(x x))
Pas de forme normale atteinte après 10 étapes de réduction


### $\beta$-équivalence

La relation $\twoheadrightarrow_\beta$ n'est pas symétrique. En effet, en général, si $T\twoheadrightarrow_\beta R$, on n'a pas $R\twoheadrightarrow_\beta T$.

En considèrant que la forme normale d'un terme normalisable représente sa « valeur », on peut définir une relation d'équivalence sur les $\lambda$-termes normalisables. Cette relation d'équivalence est la clôture symétrique de la relation de réduction $\twoheadrightarrow_\beta$.

Deux $\lambda$-termes $T$ et $S$ (normalisables ou non) sont dit $\beta$-équivalents, et on note $T=_\beta S$, s'il existe un terme $R$ tel que $T\twoheadrightarrow_\beta R$ et $S\twoheadrightarrow_\beta R$.

Ainsi deux termes normalisables ayant la même forme normale sont $\beta$-équivalents.

**Théorème du point fixe** Pour tout $\lambda$-terme $T$, il existe un $\lambda$-terme $X$ tel que

$$ (T\ X) =_\beta X.$$

La démonstration de ce théorème se fait en considérant les $\lambda$-termes
$$ W = \lambda x.(T\ (x\ x)),$$
et
$$ X = (W\ W).$$
Il est clair que
$$ X \rightarrow_\beta (T\ (W\ W)) = (T\ X),$$
et donc que
$$ X =_\beta (T\ X).$$

In [30]:
W = Lambda_terme('!x.(T (x x))')
X = W.applique(W)
print(X)
print(X.reduit()[0])

(λx.(T (x x)) λx.(T (x x)))
(T (λx.(T (x x)) λx.(T (x x))))


**Remarque** À noter que dans la démonstration du théorème du point fixe, pour établir que $(T\ X) =_\beta X$, on a montré que $X$ se réduit en $(T\ X)$ et non le contraire.

## Pouvoir d'expression du $\lambda$-calcul

Dans cette section, nous allons découvrir que le $\lambda$-calcul permet 

* de représenter les nombres entiers et de définir les opérations arithmétiques de base
* de définir des couples, listes, structures à la base de nombreuses autres structures de données
* de définir des booléens, et de simuler des expressions conditionnelles
* d'itérer des fonctions,
* d'exprimer n'importe quelle fonction récursive.

Bref, d'un certain point de vue le $\lambda$-calcul est un langage de programmation ... certes assez peu efficace comme on pourra s'en rendre compte.

### Booléens, opérateurs logiques et conditionnelles

#### Les deux booléens VRAI et FAUX

On peut représenter les deux booléens VRAI et FAUX par les $\lambda$-termes
$$ VRAI = \lambda x.\lambda y.x,$$
et
$$ FAUX = \lambda x.\lambda y.y.$$

In [31]:
VRAI = Lambda_terme('!x.!y.x')
FAUX = Lambda_terme('!x.!y.y')

#### Le terme IF

Ce choix peut être justifiée a posteriori en considérant que l'expression conditionnelle fréquente en programmation

      IF c THEN a ELSE s

peut être facilement simulée à l'aide d'abstractions des variables $c$, $a$ et $s$  par le $\lambda$-terme

$$ \mathtt{IF} = \lambda c.\lambda a.\lambda s.((c\ a)\ s).$$

In [32]:
IF = Lambda_terme('!c.!a.!s.((c a) s)') 

In [33]:
IF.applique(VRAI).applique(Lambda_terme('ALORS')).applique(Lambda_terme('SINON')).forme_normale(verbose=True)

(((λc.λa.λs.((c a) s) λx.λy.x) ALORS) SINON)
  1: ---> (((λc.λa.λs.((c a) s) λx.λy.x) ALORS) SINON)
  2: ---> ((λa.λs.((λx.λy.x a) s) ALORS) SINON)
  3: ---> (λs.((λx.λy.x ALORS) s) SINON)
  4: ---> ((λx.λy.x ALORS) SINON)
  5: ---> (λy.ALORS SINON)
  6: ---> ALORS
Forme normale calculée : ALORS


In [34]:
IF.applique(FAUX).applique(Lambda_terme('ALORS')).applique(Lambda_terme('SINON')).forme_normale(verbose=True)

(((λc.λa.λs.((c a) s) λx.λy.y) ALORS) SINON)
  1: ---> (((λc.λa.λs.((c a) s) λx.λy.y) ALORS) SINON)
  2: ---> ((λa.λs.((λx.λy.y a) s) ALORS) SINON)
  3: ---> (λs.((λx.λy.y ALORS) s) SINON)
  4: ---> ((λx.λy.y ALORS) SINON)
  5: ---> (λy.y SINON)
  6: ---> SINON
Forme normale calculée : SINON


**Remarque**
Le $\lambda$-terme $\mathtt{IF}$ permet d'exprimer des $\lambda$-termes ayant une forme normale bien que l'une ou l'autre de ses sous-termes n'en aient pas, comme par exemple

1. $(((\mathtt{IF}\, \mathtt{VRAI})\, \mathtt{ALORS})\, \mathtt{OMEGA})$  qui se réduit en $\mathtt{ALORS}$ (et a donc une forme normale si  $\mathtt{ALORS}$ en a une) bien que $\mathtt{OMEGA}$ n'en ait pas ;

2. ou $(((\mathtt{IF}\, \mathtt{FAUX})\, \mathtt{OMEGA})\, \mathtt{SINON})$ qui se réduit en  $\mathtt{SINON}$.

Cette propriété est bien utile en programmation, et servira pour la programmation de fonctions récursives.

In [35]:
IF.applique(VRAI).applique(Lambda_terme('ALORS')).applique(OMEGA).forme_normale(verbose=True)

(((λc.λa.λs.((c a) s) λx.λy.x) ALORS) (λx.(x x) λx.(x x)))
  1: ---> (((λc.λa.λs.((c a) s) λx.λy.x) ALORS) (λx.(x x) λx.(x x)))
  2: ---> ((λa.λs.((λx.λy.x a) s) ALORS) (λx.(x x) λx.(x x)))
  3: ---> (λs.((λx.λy.x ALORS) s) (λx.(x x) λx.(x x)))
  4: ---> ((λx.λy.x ALORS) (λx.(x x) λx.(x x)))
  5: ---> (λy.ALORS (λx.(x x) λx.(x x)))
  6: ---> ALORS
Forme normale calculée : ALORS


In [36]:
IF.applique(FAUX).applique(OMEGA).applique(Lambda_terme('SINON')).forme_normale(verbose=True)

(((λc.λa.λs.((c a) s) λx.λy.y) (λx.(x x) λx.(x x))) SINON)
  1: ---> (((λc.λa.λs.((c a) s) λx.λy.y) (λx.(x x) λx.(x x))) SINON)
  2: ---> ((λa.λs.((λx.λy.y a) s) (λx.(x x) λx.(x x))) SINON)
  3: ---> (λs.((λx.λy.y (λx.(x x) λx.(x x))) s) SINON)
  4: ---> ((λx.λy.y (λx.(x x) λx.(x x))) SINON)
  5: ---> (λy.y SINON)
  6: ---> SINON
Forme normale calculée : SINON


Le fait que le terme `IF` se comporte bien comme on l'attend résulte du choix de la stratégie de réduction des redex les plus à gauche en priorité. Si la stratégie choisie avait été de réduire le redex le plus à droite, la réduction de chacun des deux termes précédents aurait conduit à la tentative de réduire le terme $\Omega$ qui échoue puisque celui-ci n'est pas normalisable comme on l'a vu.

Il est facile de définir les opérateurs logiques de base : conjonction, disjonction et négation.

#### Opérateur ET

L'opérateur logique de conjonction peut être défini par

$$ ET = \lambda a.\lambda b.(((IF\ a)\ b)\ FAUX).$$

In [37]:
ET = IF.applique(Lambda_terme('a')).applique(Lambda_terme('b')).applique(FAUX).abstrait('b').abstrait('a')

In [38]:
print(ET)

λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y)


Et on peut verifier que ce terme satisfait bien à la table de vérité de l'opérateur de conjonction.

In [39]:
ET.applique(VRAI).applique(VRAI).forme_normale(verbose=True) == VRAI

((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.x) λx.λy.x)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.x) λx.λy.x)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.x) b) λx.λy.y) λx.λy.x)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.x) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.x a) s) λx.λy.x) λx.λy.y)
  5: ---> (λs.((λx.λy.x λx.λy.x) s) λx.λy.y)
  6: ---> ((λx.λy.x λx.λy.x) λx.λy.y)
  7: ---> (λy.λx.λy.x λx.λy.y)
  8: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

In [40]:
ET.applique(VRAI).applique(FAUX).forme_normale(verbose=True) == FAUX

((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.x) λx.λy.y)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.x) λx.λy.y)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.x) b) λx.λy.y) λx.λy.y)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.y) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.x a) s) λx.λy.y) λx.λy.y)
  5: ---> (λs.((λx.λy.x λx.λy.y) s) λx.λy.y)
  6: ---> ((λx.λy.x λx.λy.y) λx.λy.y)
  7: ---> (λy.λx.λy.y λx.λy.y)
  8: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

In [41]:
ET.applique(FAUX).applique(VRAI).forme_normale(verbose=True) == FAUX

((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.y) λx.λy.x)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.y) λx.λy.x)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.y) b) λx.λy.y) λx.λy.x)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.x) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.y a) s) λx.λy.x) λx.λy.y)
  5: ---> (λs.((λx.λy.y λx.λy.x) s) λx.λy.y)
  6: ---> ((λx.λy.y λx.λy.x) λx.λy.y)
  7: ---> (λy.y λx.λy.y)
  8: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

In [42]:
ET.applique(FAUX).applique(FAUX).forme_normale(verbose=True) == FAUX

((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.y) λx.λy.y)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) λx.λy.y) λx.λy.y)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.y) b) λx.λy.y) λx.λy.y)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.y) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.y a) s) λx.λy.y) λx.λy.y)
  5: ---> (λs.((λx.λy.y λx.λy.y) s) λx.λy.y)
  6: ---> ((λx.λy.y λx.λy.y) λx.λy.y)
  7: ---> (λy.y λx.λy.y)
  8: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

#### Opérateur OU

L'opérateur logique de disjonction peut être défini par

$$ OU = \lambda a.\lambda b.(((IF\ a)\ VRAI)\ b).$$

In [43]:
OU = IF.applique(Lambda_terme('a')).applique(VRAI).applique(Lambda_terme('b')).abstrait('b').abstrait('a')

In [44]:
print(OU)

λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b)


Et on peut verifier que ce terme satisfait bien à la table de vérité de l'opérateur de disjonction.

In [45]:
OU.applique(VRAI).applique(VRAI).forme_normale(verbose=True) == VRAI

((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.x) λx.λy.x)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.x) λx.λy.x)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.x) b) λx.λy.x)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.x) λx.λy.x)
  4: ---> ((λa.λs.((λx.λy.x a) s) λx.λy.x) λx.λy.x)
  5: ---> (λs.((λx.λy.x λx.λy.x) s) λx.λy.x)
  6: ---> ((λx.λy.x λx.λy.x) λx.λy.x)
  7: ---> (λy.λx.λy.x λx.λy.x)
  8: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

In [46]:
OU.applique(VRAI).applique(FAUX).forme_normale(verbose=True) == VRAI

((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.x) λx.λy.y)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.x) λx.λy.y)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.x) b) λx.λy.y)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.x) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.x a) s) λx.λy.x) λx.λy.y)
  5: ---> (λs.((λx.λy.x λx.λy.x) s) λx.λy.y)
  6: ---> ((λx.λy.x λx.λy.x) λx.λy.y)
  7: ---> (λy.λx.λy.x λx.λy.y)
  8: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

In [47]:
OU.applique(FAUX).applique(VRAI).forme_normale(verbose=True) == VRAI

((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.y) λx.λy.x)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.y) λx.λy.x)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.x) b) λx.λy.x)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.x) λx.λy.x)
  4: ---> ((λa.λs.((λx.λy.y a) s) λx.λy.x) λx.λy.x)
  5: ---> (λs.((λx.λy.y λx.λy.x) s) λx.λy.x)
  6: ---> ((λx.λy.y λx.λy.x) λx.λy.x)
  7: ---> (λy.y λx.λy.x)
  8: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

In [48]:
OU.applique(FAUX).applique(FAUX).forme_normale(verbose=True) == FAUX

((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.y) λx.λy.y)
  1: ---> ((λa.λb.(((λc.λa.λs.((c a) s) a) λx.λy.x) b) λx.λy.y) λx.λy.y)
  2: ---> (λb.(((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.x) b) λx.λy.y)
  3: ---> (((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.x) λx.λy.y)
  4: ---> ((λa.λs.((λx.λy.y a) s) λx.λy.x) λx.λy.y)
  5: ---> (λs.((λx.λy.y λx.λy.x) s) λx.λy.y)
  6: ---> ((λx.λy.y λx.λy.x) λx.λy.y)
  7: ---> (λy.y λx.λy.y)
  8: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

#### Opérateur NON

L'opérateur de négation peut être défini par le terme

$$ NON = \lambda a.(((IF\ a)\ FAUX)\ VRAI).$$

In [49]:
NON = IF.applique(Lambda_terme('a')).applique(FAUX).applique(VRAI).abstrait('a')

In [50]:
print(NON)

λa.(((λc.λa.λs.((c a) s) a) λx.λy.y) λx.λy.x)


In [51]:
NON.applique(VRAI).forme_normale(verbose=True) == FAUX

(λa.(((λc.λa.λs.((c a) s) a) λx.λy.y) λx.λy.x) λx.λy.x)
  1: ---> (λa.(((λc.λa.λs.((c a) s) a) λx.λy.y) λx.λy.x) λx.λy.x)
  2: ---> (((λc.λa.λs.((c a) s) λx.λy.x) λx.λy.y) λx.λy.x)
  3: ---> ((λa.λs.((λx.λy.x a) s) λx.λy.y) λx.λy.x)
  4: ---> (λs.((λx.λy.x λx.λy.y) s) λx.λy.x)
  5: ---> ((λx.λy.x λx.λy.y) λx.λy.x)
  6: ---> (λy.λx.λy.y λx.λy.x)
  7: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

In [52]:
NON.applique(FAUX).forme_normale(verbose=True) == VRAI

(λa.(((λc.λa.λs.((c a) s) a) λx.λy.y) λx.λy.x) λx.λy.y)
  1: ---> (λa.(((λc.λa.λs.((c a) s) a) λx.λy.y) λx.λy.x) λx.λy.y)
  2: ---> (((λc.λa.λs.((c a) s) λx.λy.y) λx.λy.y) λx.λy.x)
  3: ---> ((λa.λs.((λx.λy.y a) s) λx.λy.y) λx.λy.x)
  4: ---> (λs.((λx.λy.y λx.λy.y) s) λx.λy.x)
  5: ---> ((λx.λy.y λx.λy.y) λx.λy.x)
  6: ---> (λy.y λx.λy.x)
  7: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

### Entiers, successeurs, addition, multiplication et exponentiation

#### Numéraux de Church

Il existe plusieurs façons de représenter les entiers naturels par un $\lambda$-terme. La représentation donnée ici est connue sous le nom de *numéraux de Church*.

In [53]:
ZERO = Lambda_terme('!f.!x.x')

In [54]:
UN = Lambda_terme('!f.!x.(f x)')

In [55]:
DEUX = Lambda_terme('!f.!x.(f (f x))')

#### Successeur

In [56]:
SUC = Lambda_terme('!n.!f.!x.(f ((n f) x))')

In [57]:
TROIS = SUC.applique(DEUX).forme_normale(verbose=True)

(λn.λf.λx.(f ((n f) x)) λf.λx.(f (f x)))
  1: ---> (λn.λf.λx.(f ((n f) x)) λf.λx.(f (f x)))
  2: ---> λf.λx.(f ((λf.λx.(f (f x)) f) x))
  3: ---> λf.λx.(f (λx.(f (f x)) x))
  4: ---> λf.λx.(f (f (f x)))
Forme normale calculée : λf.λx.(f (f (f x)))


In [58]:
TROIS.applique(SUC).applique(ZERO).forme_normale(verbose=True)

((λf.λx.(f (f (f x))) λn.λf.λx.(f ((n f) x))) λf.λx.x)
  1: ---> ((λf.λx.(f (f (f x))) λn.λf.λx.(f ((n f) x))) λf.λx.x)
  2: ---> (λx.(λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) x))) λf.λx.x)
  3: ---> (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) λf.λx.x)))
  4: ---> λf.λx.(f (((λn.λf.λx.(f ((n f) x)) (λn.λf.λx.(f ((n f) x)) λf.λx.x)) f) x))
  5: ---> λf.λx.(f ((λf.λx.(f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)) f) x))
  6: ---> λf.λx.(f (λx.(f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)) x))
  7: ---> λf.λx.(f (f (((λn.λf.λx.(f ((n f) x)) λf.λx.x) f) x)))
  8: ---> λf.λx.(f (f ((λf.λx.(f ((λf.λx.x f) x)) f) x)))
  9: ---> λf.λx.(f (f (λx.(f ((λf.λx.x f) x)) x)))
 10: ---> λf.λx.(f (f (f ((λf.λx.x f) x))))
 11: ---> λf.λx.(f (f (f (λx.x x))))
 12: ---> λf.λx.(f (f (f x)))
Forme normale calculée : λf.λx.(f (f (f x)))


#### Addition

In [59]:
ADD = Lambda_terme('!n.!m.!f.!x.((n f) ((m f) x))')

In [60]:
QUATRE = ADD.applique(UN).applique(TROIS).forme_normale(verbose=True)

((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f x)) λf.λx.(f (f (f x))))
  1: ---> ((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f x)) λf.λx.(f (f (f x))))
  2: ---> (λm.λf.λx.((λf.λx.(f x) f) ((m f) x)) λf.λx.(f (f (f x))))
  3: ---> λf.λx.((λf.λx.(f x) f) ((λf.λx.(f (f (f x))) f) x))
  4: ---> λf.λx.(λx.(f x) ((λf.λx.(f (f (f x))) f) x))
  5: ---> λf.λx.(f ((λf.λx.(f (f (f x))) f) x))
  6: ---> λf.λx.(f (λx.(f (f (f x))) x))
  7: ---> λf.λx.(f (f (f (f x))))
Forme normale calculée : λf.λx.(f (f (f (f x))))


In [61]:
CINQ = ADD.applique(TROIS).applique(DEUX).forme_normale(verbose=True)

((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f (f (f x)))) λf.λx.(f (f x)))
  1: ---> ((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f (f (f x)))) λf.λx.(f (f x)))
  2: ---> (λm.λf.λx.((λf.λx.(f (f (f x))) f) ((m f) x)) λf.λx.(f (f x)))
  3: ---> λf.λx.((λf.λx.(f (f (f x))) f) ((λf.λx.(f (f x)) f) x))
  4: ---> λf.λx.(λx.(f (f (f x))) ((λf.λx.(f (f x)) f) x))
  5: ---> λf.λx.(f (f (f ((λf.λx.(f (f x)) f) x))))
  6: ---> λf.λx.(f (f (f (λx.(f (f x)) x))))
  7: ---> λf.λx.(f (f (f (f (f x)))))
Forme normale calculée : λf.λx.(f (f (f (f (f x)))))


In [62]:
SEPT = ADD.applique(QUATRE).applique(TROIS).forme_normale(verbose=True)

((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f (f (f (f x))))) λf.λx.(f (f (f x))))
  1: ---> ((λn.λm.λf.λx.((n f) ((m f) x)) λf.λx.(f (f (f (f x))))) λf.λx.(f (f (f x))))
  2: ---> (λm.λf.λx.((λf.λx.(f (f (f (f x)))) f) ((m f) x)) λf.λx.(f (f (f x))))
  3: ---> λf.λx.((λf.λx.(f (f (f (f x)))) f) ((λf.λx.(f (f (f x))) f) x))
  4: ---> λf.λx.(λx.(f (f (f (f x)))) ((λf.λx.(f (f (f x))) f) x))
  5: ---> λf.λx.(f (f (f (f ((λf.λx.(f (f (f x))) f) x)))))
  6: ---> λf.λx.(f (f (f (f (λx.(f (f (f x))) x)))))
  7: ---> λf.λx.(f (f (f (f (f (f (f x)))))))
Forme normale calculée : λf.λx.(f (f (f (f (f (f (f x)))))))


#### Multiplication

In [63]:
MUL = Lambda_terme('!n.!m.!f.(n (m f))')

In [64]:
SIX = MUL.applique(DEUX).applique(TROIS).forme_normale(verbose=True)

((λn.λm.λf.(n (m f)) λf.λx.(f (f x))) λf.λx.(f (f (f x))))
  1: ---> ((λn.λm.λf.(n (m f)) λf.λx.(f (f x))) λf.λx.(f (f (f x))))
  2: ---> (λm.λf.(λf.λx.(f (f x)) (m f)) λf.λx.(f (f (f x))))
  3: ---> λf.(λf.λx.(f (f x)) (λf.λx.(f (f (f x))) f))
  4: ---> λf.λx.((λf.λx.(f (f (f x))) f) ((λf.λx.(f (f (f x))) f) x))
  5: ---> λf.λx.(λx.(f (f (f x))) ((λf.λx.(f (f (f x))) f) x))
  6: ---> λf.λx.(f (f (f ((λf.λx.(f (f (f x))) f) x))))
  7: ---> λf.λx.(f (f (f (λx.(f (f (f x))) x))))
  8: ---> λf.λx.(f (f (f (f (f (f x))))))
Forme normale calculée : λf.λx.(f (f (f (f (f (f x))))))


#### Exponentiation

In [65]:
EXP = Lambda_terme('!n.!m.(m n)')

In [66]:
HUIT = EXP.applique(DEUX).applique(TROIS).forme_normale(verbose=True)

((λn.λm.(m n) λf.λx.(f (f x))) λf.λx.(f (f (f x))))
  1: ---> ((λn.λm.(m n) λf.λx.(f (f x))) λf.λx.(f (f (f x))))
  2: ---> (λm.(m λf.λx.(f (f x))) λf.λx.(f (f (f x))))
  3: ---> (λf.λx.(f (f (f x))) λf.λx.(f (f x)))
  4: ---> λx.(λf.λx.(f (f x)) (λf.λx.(f (f x)) (λf.λx.(f (f x)) x)))
  5: ---> λx.λx0.((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0))
  6: ---> λx.λx0.(λx0.((λf.λx.(f (f x)) x) ((λf.λx.(f (f x)) x) x0)) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0))
  7: ---> λx.λx0.((λf.λx.(f (f x)) x) ((λf.λx.(f (f x)) x) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0)))
  8: ---> λx.λx0.(λx0.(x (x x0)) ((λf.λx.(f (f x)) x) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0)))
  9: ---> λx.λx0.(x (x ((λf.λx.(f (f x)) x) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0))))
 10: ---> λx.λx0.(x (x (λx0.(x (x x0)) ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0))))
 11: ---> λx.λx0.(x (x (x (x ((λf.λx.(f (f x)) (λf.λx.(f (f x)) x)) x0)))))
 12: ---> λx.λx0.(x (x (x (x (λx0.((λf.λx.(f (f

In [67]:
HUIT == MUL.applique(DEUX).applique(QUATRE).forme_normale()

True

In [68]:
NEUF = EXP.applique(TROIS).applique(DEUX).forme_normale(verbose=True)

((λn.λm.(m n) λf.λx.(f (f (f x)))) λf.λx.(f (f x)))
  1: ---> ((λn.λm.(m n) λf.λx.(f (f (f x)))) λf.λx.(f (f x)))
  2: ---> (λm.(m λf.λx.(f (f (f x)))) λf.λx.(f (f x)))
  3: ---> (λf.λx.(f (f x)) λf.λx.(f (f (f x))))
  4: ---> λx.(λf.λx.(f (f (f x))) (λf.λx.(f (f (f x))) x))
  5: ---> λx.λx0.((λf.λx.(f (f (f x))) x) ((λf.λx.(f (f (f x))) x) ((λf.λx.(f (f (f x))) x) x0)))
  6: ---> λx.λx0.(λx0.(x (x (x x0))) ((λf.λx.(f (f (f x))) x) ((λf.λx.(f (f (f x))) x) x0)))
  7: ---> λx.λx0.(x (x (x ((λf.λx.(f (f (f x))) x) ((λf.λx.(f (f (f x))) x) x0)))))
  8: ---> λx.λx0.(x (x (x (λx0.(x (x (x x0))) ((λf.λx.(f (f (f x))) x) x0)))))
  9: ---> λx.λx0.(x (x (x (x (x (x ((λf.λx.(f (f (f x))) x) x0)))))))
 10: ---> λx.λx0.(x (x (x (x (x (x (λx0.(x (x (x x0))) x0)))))))
 11: ---> λx.λx0.(x (x (x (x (x (x (x (x (x x0)))))))))
Forme normale calculée : λx.λx0.(x (x (x (x (x (x (x (x (x x0)))))))))


In [69]:
NEUF == ADD.applique(SEPT).applique(DEUX).forme_normale()

True

#### Nullité

In [70]:
NUL = Lambda_terme('!n.((n !x.FAUX) VRAI)').subs('FAUX', FAUX).subs('VRAI', VRAI)

In [71]:
print(NUL)

λn.((n λx.λx.λy.y) λx.λy.x)


In [72]:
NUL.applique(ZERO).forme_normale(verbose=True) == VRAI

(λn.((n λx.λx.λy.y) λx.λy.x) λf.λx.x)
  1: ---> (λn.((n λx.λx.λy.y) λx.λy.x) λf.λx.x)
  2: ---> ((λf.λx.x λx.λx.λy.y) λx.λy.x)
  3: ---> (λx.x λx.λy.x)
  4: ---> λx.λy.x
Forme normale calculée : λx.λy.x


True

In [73]:
NUL.applique(TROIS).forme_normale(verbose=True) == FAUX

(λn.((n λx.λx.λy.y) λx.λy.x) λf.λx.(f (f (f x))))
  1: ---> (λn.((n λx.λx.λy.y) λx.λy.x) λf.λx.(f (f (f x))))
  2: ---> ((λf.λx.(f (f (f x))) λx.λx.λy.y) λx.λy.x)
  3: ---> (λx.(λx.λx.λy.y (λx.λx.λy.y (λx.λx.λy.y x))) λx.λy.x)
  4: ---> (λx.λx.λy.y (λx.λx.λy.y (λx.λx.λy.y λx.λy.x)))
  5: ---> λx.λy.y
Forme normale calculée : λx.λy.y


True

### Couples et listes

In [74]:
CONS = Lambda_terme('!x.!y.!s.(((IF s) x) y)').subs('IF', IF)

In [75]:
print(CONS)

λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y)


In [76]:
UN_DEUX = CONS.applique(UN).applique(DEUX).forme_normale(verbose=True)

((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.(f x)) λf.λx.(f (f x)))
  1: ---> ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.(f x)) λf.λx.(f (f x)))
  2: ---> (λy.λs.(((λc.λa.λs.((c a) s) s) λf.λx.(f x)) y) λf.λx.(f (f x)))
  3: ---> λs.(((λc.λa.λs.((c a) s) s) λf.λx.(f x)) λf.λx.(f (f x)))
  4: ---> λs.((λa.λs0.((s a) s0) λf.λx.(f x)) λf.λx.(f (f x)))
  5: ---> λs.(λs0.((s λf.λx.(f x)) s0) λf.λx.(f (f x)))
  6: ---> λs.((s λf.λx.(f x)) λf.λx.(f (f x)))
Forme normale calculée : λs.((s λf.λx.(f x)) λf.λx.(f (f x)))


In [77]:
CAR = Lambda_terme('!c.(c VRAI)').subs('VRAI', VRAI)

In [78]:
print(CAR)

λc.(c λx.λy.x)


In [79]:
CAR.applique(UN_DEUX).forme_normale(verbose=True) == UN

(λc.(c λx.λy.x) λs.((s λf.λx.(f x)) λf.λx.(f (f x))))
  1: ---> (λc.(c λx.λy.x) λs.((s λf.λx.(f x)) λf.λx.(f (f x))))
  2: ---> (λs.((s λf.λx.(f x)) λf.λx.(f (f x))) λx.λy.x)
  3: ---> ((λx.λy.x λf.λx.(f x)) λf.λx.(f (f x)))
  4: ---> (λy.λf.λx.(f x) λf.λx.(f (f x)))
  5: ---> λf.λx.(f x)
Forme normale calculée : λf.λx.(f x)


True

In [80]:
CDR = Lambda_terme('!c.(c FAUX)').subs('FAUX', FAUX)

In [81]:
print(CDR)

λc.(c λx.λy.y)


In [82]:
CDR.applique(UN_DEUX).forme_normale(verbose=True) == DEUX

(λc.(c λx.λy.y) λs.((s λf.λx.(f x)) λf.λx.(f (f x))))
  1: ---> (λc.(c λx.λy.y) λs.((s λf.λx.(f x)) λf.λx.(f (f x))))
  2: ---> (λs.((s λf.λx.(f x)) λf.λx.(f (f x))) λx.λy.y)
  3: ---> ((λx.λy.y λf.λx.(f x)) λf.λx.(f (f x)))
  4: ---> (λy.y λf.λx.(f (f x)))
  5: ---> λf.λx.(f (f x))
Forme normale calculée : λf.λx.(f (f x))


True

In [83]:
M = Lambda_terme('M')
CPLE_M = CONS.applique(CAR.applique(M)).applique(CDR.applique(M))

In [84]:
CDR.applique(CPLE_M).forme_normale(verbose=True)

(λc.(c λx.λy.y) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M)))
  1: ---> (λc.(c λx.λy.y) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M)))
  2: ---> (((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M)) λx.λy.y)
  3: ---> ((λy.λs.(((λc.λa.λs.((c a) s) s) (λc.(c λx.λy.x) M)) y) (λc.(c λx.λy.y) M)) λx.λy.y)
  4: ---> (λs.(((λc.λa.λs.((c a) s) s) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M)) λx.λy.y)
  5: ---> (((λc.λa.λs.((c a) s) λx.λy.y) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M))
  6: ---> ((λa.λs.((λx.λy.y a) s) (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M))
  7: ---> (λs.((λx.λy.y (λc.(c λx.λy.x) M)) s) (λc.(c λx.λy.y) M))
  8: ---> ((λx.λy.y (λc.(c λx.λy.x) M)) (λc.(c λx.λy.y) M))
  9: ---> (λy.y (λc.(c λx.λy.y) M))
 10: ---> (λc.(c λx.λy.y) M)
 11: ---> (M λx.λy.y)
Forme normale calculée : (M λx.λy.y)


In [85]:
M_PRED = Lambda_terme('!n.(CAR ((n !c.((CONS (CDR c)) (SUC (CDR c)))) ((CONS ZERO) ZERO)))')
print(M_PRED)
PRED = M_PRED.subs('CAR', CAR).subs('CONS', CONS).subs('CDR', CDR).subs('SUC', SUC).subs('ZERO', ZERO)
print(PRED)

λn.(CAR ((n λc.((CONS (CDR c)) (SUC (CDR c)))) ((CONS ZERO) ZERO)))
λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))


In [86]:
PRED.applique(DEUX).forme_normale(verbose=True) == UN

(λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) λf.λx.(f (f x)))
  1: ---> (λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) λf.λx.(f (f x)))
  2: ---> (λc.(c λx.λy.x) ((λf.λx.(f (f x)) λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))
  3: ---> (((λf.λx.(f (f x)) λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)) λx.λy.x)
  4: ---> ((λx.(λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c))) (λc.((λx.

True

In [87]:
PRED.applique(ZERO).forme_normale(verbose=True) == ZERO

(λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) λf.λx.x)
  1: ---> (λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) λf.λx.x)
  2: ---> (λc.(c λx.λy.x) ((λf.λx.x λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))
  3: ---> (((λf.λx.x λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)) λx.λy.x)
  4: ---> ((λx.x ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)) λx.λy.x)
  5: ---> (((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x) λx.λy.x)


True

In [88]:
M_SUB = Lambda_terme('!n.!m.((m PRED) n)')
print(M_SUB)
SUB = M_SUB.subs('PRED', PRED)
print(SUB)

λn.λm.((m PRED) n)
λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n)


In [89]:
SUB.applique(TROIS).applique(UN).forme_normale(verbose=True) == DEUX

((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) λf.λx.(f (f (f x)))) λf.λx.(f x))
  1: ---> ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) λf.λx.(f (f (f x)))) λf.λx.(f x))
  2: ---> (λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) λf.λx.(f (f (f x)))) λf.λx.(f x))
  3: ---> ((λf.λx.(f x) λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) λf.λx.(f (f (f x))))
  4: --

True

In [90]:
M_INF = Lambda_terme('!n.!m.(NUL ((SUB n) m))')
print(M_INF)
INF = M_INF.subs('NUL', NUL).subs('SUB', SUB)

λn.λm.(NUL ((SUB n) m))


In [91]:
INF.applique(TROIS).applique(UN).forme_normale() == FAUX

True

In [92]:
INF.applique(UN).applique(TROIS).forme_normale() == VRAI

True

In [93]:
INF.applique(UN).applique(UN).forme_normale() == VRAI

True

In [94]:
M_EGAL = Lambda_terme('!n.!m.((ET ((INF n) m)) ((INF m) n))')
print(M_EGAL)
EGAL = M_EGAL.subs('ET', ET).subs('INF', INF)
print(EGAL)

λn.λm.((ET ((INF n) m)) ((INF m) n))
λn.λm.((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) n) m)) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) m) n))


In [95]:
EGAL.applique(UN).applique(UN).forme_normale() == VRAI

True

In [96]:
EGAL.applique(UN).applique(DEUX).forme_normale() == FAUX

True

### Itération

In [97]:
M_FACTv1 = Lambda_terme('!n.(CDR ((n !c.((CONS (SUC (CAR c))) ((MUL (SUC (CAR c))) (CDR c)))) ((CONS ZERO) UN)))')
print(M_FACTv1)
FACTv1 = M_FACTv1.subs('CONS', CONS).subs('CAR', CAR).subs('CDR', CDR).subs('SUC', SUC).subs('MUL', MUL).subs('UN', UN).subs('ZERO', ZERO)
print(FACTv1)

λn.(CDR ((n λc.((CONS (SUC (CAR c))) ((MUL (SUC (CAR c))) (CDR c)))) ((CONS ZERO) UN)))
λn.(λc.(c λx.λy.y) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.x) c))) ((λn.λm.λf.(n (m f)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.x) c))) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.(f x))))


In [98]:
FACTv1.applique(ZERO).forme_normale() == UN

True

In [99]:
FACTv1.applique(UN).forme_normale() == UN

True

In [100]:
print(FACTv1.applique(DEUX).forme_normale())

None


In [101]:
FACTv1.applique(DEUX).forme_normale(nb_etapes_max=118) == DEUX

True

In [102]:
FACTv1.applique(TROIS).forme_normale(nb_etapes_max=403) == SIX

True

In [103]:
FACTv1.applique(QUATRE).forme_normale(nb_etapes_max=1672) == MUL.applique(QUATRE).applique(SIX).forme_normale()

True

### Et la récursivité ? 

In [104]:
M_PHI_FACT = Lambda_terme('!f.!n.(((IF ((EGAL n) ZERO)) UN) ((MUL n) (f (PRED n))))')
print(M_PHI_FACT)
PHI_FACT = M_PHI_FACT.subs('IF', IF).subs('EGAL', EGAL).subs('ZERO', ZERO).subs('UN', UN).subs('MUL', MUL).subs('PRED', PRED)
print(PHI_FACT)

λf.λn.(((IF ((EGAL n) ZERO)) UN) ((MUL n) (f (PRED n))))
λf.λn.(((λc.λa.λs.((c a) s) ((λn.λm.((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) n) m)) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) m) n)) n) λf.λx.x)) λf.λx.(f x)) ((λn.λm.λf.(n (m f)) n) (f (λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) n))))


In [105]:
BOTTOM = Lambda_terme('!y.OMEGA').subs('OMEGA', OMEGA)
print(BOTTOM)

λy.(λx.(x x) λx.(x x))


In [106]:
FACT0 = PHI_FACT.applique(BOTTOM)

In [107]:
FACT0.applique(ZERO).forme_normale() == UN

True

In [108]:
FACT0.applique(UN).forme_normale(verbose=True, nb_etapes_max=20)

((λf.λn.(((λc.λa.λs.((c a) s) ((λn.λm.((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) n) m)) ((λn.λm.(λn.((n λx.λx.λy.y) λx.λy.x) ((λn.λm.((m λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x)))) n) n) m)) m) n)) n) λf.λx.x)) λf.λx.(f x)) ((λn.λm.λf.(n (m f)) n) (f (λn.(λc.(c λx.λy.x) ((n λc.((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) (λc.(c λx.λy.y) c)) (λn.λf.λx.(f ((n f) x)) (λc.(c λx.λy.y) c)))) ((λx.λy.λs.(((λc.λa.λs.((c a) s) s) x) y) λf.λx.x) λf.λx.x))) n)))) λy.(λx.(x x) λx.(x x))) λf.λx.(f x))
  1: ---> ((λf.λn.(((λc.λa.λs.((c a) s) ((λn.λm.((λa.λb.(((λc.λa.λs.((c a) s) a) b) λx.λy.y) ((λn.

In [109]:
FACT1 = PHI_FACT.applique(FACT0)

In [110]:
FACT1.applique(ZERO).forme_normale() == UN

True

In [111]:
FACT1.applique(UN).forme_normale(nb_etapes_max=110) == UN

True

In [112]:
FIX_CURRY = Lambda_terme('!f.(!x.(f (x x)) !x.(f (x x)))')
print(FIX_CURRY)

λf.(λx.(f (x x)) λx.(f (x x)))


In [113]:
FACTv2 = FIX_CURRY.applique(PHI_FACT)

In [114]:
FACTv2.applique(ZERO).forme_normale() == UN

True

In [115]:
FACTv2.applique(UN).forme_normale(nb_etapes_max=113) == UN

True

In [116]:
FACTv2.applique(DEUX).forme_normale(nb_etapes_max=516) == DEUX

True

In [117]:
FACTv2.applique(TROIS).forme_normale(nb_etapes_max=2882) == SIX

True

In [118]:
FACTv2.applique(QUATRE).forme_normale(nb_etapes_max=18668) == MUL.applique(QUATRE).applique(SIX).forme_normale()

True

In [119]:
PF = FIX_CURRY.applique(Lambda_terme('M'))

In [120]:
PF.forme_normale(verbose=True, nb_etapes_max=10)

(λf.(λx.(f (x x)) λx.(f (x x))) M)
  1: ---> (λf.(λx.(f (x x)) λx.(f (x x))) M)
  2: ---> (λx.(M (x x)) λx.(M (x x)))
  3: ---> (M (λx.(M (x x)) λx.(M (x x))))
  4: ---> (M (M (λx.(M (x x)) λx.(M (x x)))))
  5: ---> (M (M (M (λx.(M (x x)) λx.(M (x x))))))
  6: ---> (M (M (M (M (λx.(M (x x)) λx.(M (x x)))))))
  7: ---> (M (M (M (M (M (λx.(M (x x)) λx.(M (x x))))))))
  8: ---> (M (M (M (M (M (M (λx.(M (x x)) λx.(M (x x)))))))))
  9: ---> (M (M (M (M (M (M (M (λx.(M (x x)) λx.(M (x x))))))))))
 10: ---> (M (M (M (M (M (M (M (M (λx.(M (x x)) λx.(M (x x)))))))))))
Pas de forme normale atteinte après 10 étapes de réduction


In [121]:
FIX_TURING = Lambda_terme('(!x.!y.(y ((x x) y)) !x.!y.(y ((x x) y)))')
print(FIX_TURING)

(λx.λy.(y ((x x) y)) λx.λy.(y ((x x) y)))


In [122]:
FACTv3 = FIX_TURING.applique(PHI_FACT)

In [123]:
FACTv3.applique(ZERO).forme_normale() == UN

True

In [124]:
FACTv3.applique(UN).forme_normale(nb_etapes_max=114) == UN

True

In [125]:
FACTv3.applique(DEUX).forme_normale(nb_etapes_max=520) == DEUX

True

In [126]:
FACTv3.applique(TROIS).forme_normale(nb_etapes_max=2897) == SIX

True

In [127]:
FACTv3.applique(QUATRE).forme_normale(nb_etapes_max=18732) == MUL.applique(QUATRE).applique(SIX).forme_normale()

True

# $\lambda$-calcul avec les lambda-expressions de Python

Dans cette partie, les lambda-expressions de Python vont être utilisées pour représenter les abstractions, et les applications seront des appels de fonction.

Les seuls mots du langage Python que nous utiliserons seront `lambda` et `if`. Les autres mots (`def`, `while`, `for` ...) seront bannis. Nous utiliserons aussi les entiers prédéfinis dans le langage avec certaines opérations arithmétiques.

## Les booléens

In [128]:
vrai = lambda x: lambda y: x
faux = lambda x: lambda y: y

In [129]:
def booleen_en_bool(b):
    return b(True)(False)

In [130]:
tuple(booleen_en_bool(b) for b in (vrai, faux))

(True, False)

In [131]:
If = lambda c: lambda a: lambda s: c(a)(s) 

In [132]:
If(vrai)(1)(2)

1

In [133]:
If(faux)(1)(2)

2

In [134]:
#If(vrai)(1)(1/0)

In [135]:
non = lambda b: If(b)(faux)(vrai)

In [136]:
tuple(booleen_en_bool(non(b)) for b in (vrai, faux))

(False, True)

In [137]:
et = lambda b1: lambda b2: If(b1)(b2)(faux)

In [138]:
tuple(booleen_en_bool(et(b1)(b2)) for b1 in (vrai, faux) 
      for b2 in (vrai, faux))

(True, False, False, False)

In [139]:
ou = lambda b1: lambda b2: If(b1)(vrai)(b2)

In [140]:
tuple(booleen_en_bool(ou(b1)(b2)) for b1 in (vrai, faux) 
      for b2 in (vrai, faux))

(True, True, True, False)

## Les entiers de Church

In [141]:
zero = lambda f: lambda x: x

In [142]:
un = lambda f: lambda x: f(x)

In [143]:
deux = lambda f: lambda x: f(f(x))

In [144]:
trois = lambda f: lambda x: f(f(f(x)))

In [145]:
def entier_church_en_int(ec):
    return ec(lambda n: n+1)(0)

In [146]:
tuple(entier_church_en_int(n) for n in (zero, un, deux, trois))

(0, 1, 2, 3)

In [147]:
suc = lambda n: lambda f: lambda x: f(n(f)(x))

In [148]:
tuple(entier_church_en_int(suc(n)) for n in (zero, un, deux, trois)) 

(1, 2, 3, 4)

In [149]:
def int_en_entier_church(n):
    if n == 0:
        return zero
    else:
        return suc(int_en_entier_church(n - 1))

In [150]:
tuple(entier_church_en_int(int_en_entier_church(n)) for n in range(10))

(0, 1, 2, 3, 4, 5, 6, 7, 8, 9)

In [151]:
add = lambda n: lambda m: lambda f: lambda x: n(f)(m(f)(x))

In [152]:
cinq = add(deux)(trois)
entier_church_en_int(cinq)

5

In [153]:
mul = lambda n: lambda m: lambda f: n(m(f))

In [154]:
six = mul(deux)(trois)
entier_church_en_int(six)

6

In [155]:
exp = lambda n: lambda m: m(n)

In [156]:
huit = exp(deux)(trois)
entier_church_en_int(huit)

8

In [157]:
neuf = exp(trois)(deux)
entier_church_en_int(neuf)

9

In [158]:
est_nul = lambda n : n(lambda x: faux)(vrai)

In [159]:
tuple(booleen_en_bool(est_nul(n)) 
      for n in (zero, un, deux, trois, cinq, six, huit))

(True, False, False, False, False, False, False)

## Les couples

In [160]:
cons = lambda x: lambda y: lambda z: z(x)(y)

In [161]:
un_deux = cons(un)(deux)

In [162]:
car = lambda c: c(vrai)
cdr = lambda c: c(faux)

In [163]:
entier_church_en_int(car(un_deux)), entier_church_en_int(cdr(un_deux))

(1, 2)

In [164]:
pred = lambda n: car(n(lambda c: cons(cdr(c))(suc(cdr(c))))(cons(zero)(zero)))

In [165]:
tuple(entier_church_en_int(pred(int_en_entier_church(n))) for n in range(10))

(0, 0, 1, 2, 3, 4, 5, 6, 7, 8)

In [166]:
sub = lambda n: lambda m: m(pred)(n)

In [167]:
entier_church_en_int(sub(huit)(trois))

5

In [168]:
est_inf_ou_egal = lambda n: lambda m: est_nul(sub(m)(n))

In [169]:
tuple(booleen_en_bool(est_inf_ou_egal(cinq)(int_en_entier_church(n))) 
      for n in range(10))

(True, True, True, True, True, True, False, False, False, False)

In [170]:
est_egal = lambda n: lambda m: et(est_inf_ou_egal(n)(m))(est_inf_ou_egal(m)(n))

In [171]:
tuple(booleen_en_bool(est_egal(cinq)(int_en_entier_church(n))) 
      for n in range(10))

(False, False, False, False, False, True, False, False, False, False)

## Itération

In [172]:
fact = lambda n: cdr(n(lambda c: (cons(suc(car(c)))(mul(suc(car(c)))(cdr(c)))))(cons(zero)(un)))

In [173]:
tuple(entier_church_en_int(fact(int_en_entier_church(n))) for n in range(7))

(1, 1, 2, 6, 24, 120, 720)

## Combinateur de point fixe

In [174]:
phi_fact = lambda f: lambda n: 1 if n == 0 else n*f(n-1)

In [175]:
bottom = lambda x: (lambda y: y(y))(lambda y:y(y))

In [176]:
f0 = phi_fact(bottom)
f1 = phi_fact(f0)
f2 = phi_fact(f1)
f3 = phi_fact(f2)
f4 = phi_fact(f3)

In [177]:
tuple(f4(n) for n in range(4))

(1, 1, 2, 6)

In [178]:
def fact_rec(n):
    if n == 0:
        return 1
    else:
        return n * fact_rec(n - 1)

In [179]:
fact2 = phi_fact(fact_rec)

In [180]:
tuple(fact2(n) for n in range(7))

(1, 1, 2, 6, 24, 120, 720)

In [181]:
fix_curry = lambda f: (lambda x: lambda y: f(x(x))(y))(lambda x: lambda y: f(x(x))(y))

In [182]:
fact3 = fix_curry(phi_fact)

In [183]:
tuple(fact3(n) for n in range(7))

(1, 1, 2, 6, 24, 120, 720)

## Un programme obscur

In [184]:
print((lambda x: (lambda y: lambda z: x(y(y))(z))(lambda y: lambda z: x(y(y))(z))) 
      (lambda x: lambda y: '' if y == [] else chr(y[0])+x(y[1:]))
      (((lambda x: (lambda y: lambda z: x(y(y))(z)) (lambda y: lambda z: x(y(y))(z)))
        (lambda x: lambda y: lambda z: [] if z == [] else [y(z[0])]+x(y)(z[1:])))      
       (lambda x: (lambda x: (lambda y: lambda z: x(y(y))(z))(lambda y: lambda z: x(y(y))(z)))
        (lambda x: lambda y: lambda z: lambda t: 1 if t == 0 else (lambda x: ((lambda u: 1 if u == 0 else z)(t % 2)) * x * x % y)
         (x(y)(z)(t // 2)))(989)(x)(761))
       ([377, 900, 27, 27, 182, 647, 163, 182, 390, 27, 726, 937])))

hello world!


In [185]:
phiListEnChaine = lambda x: lambda y: '' if y == [] else chr(y[0]) + x(y[1:])

In [186]:
fix_curry(phiListEnChaine)([65+k for k in range(26)])

'ABCDEFGHIJKLMNOPQRSTUVWXYZ'

In [187]:
phiMap = lambda x: lambda y: lambda z: [] if z == [] else [y(z[0])] + x(y)(z[1:])

In [188]:
fix_curry(phiMap)(lambda x: x*x)([1, 2, 3, 4])

[1, 4, 9, 16]

In [189]:
phiExpoMod = lambda x: lambda y: lambda z: lambda t: 1 if z == 0 else (lambda u: 1 if u == 0 else y)(z % 2) * x(y)(z//2)(t) ** 2 % t

In [190]:
fix_curry(phiExpoMod)(2)(10)(1000)

24